Importing the necessary libraries

In [1]:
!pip install -U "tensorflow-text==2.13.*"
!pip install "tf-models-official==2.13.*"

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.5/6.5 MB 6.7 MB/s eta 0:00:00m eta 0:00:010:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 479.7/479.7 MB 2.3 MB/s eta 0:00:00m eta 0:00:010:00:05
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.7/1.7 MB 7.8 MB/s eta 0:00:00m eta 0:00:010:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.8/4.8 MB 8.4 MB/s eta 0:00:00m eta 0:00:010:01:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.5/57.5 KB 3.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.5/24.5 MB 6.9 MB/s eta 0:00:00m eta 0:00:010:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 65.5/65.5 KB 4.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 17.3/17.3 MB 13.6 MB/s eta 0:00:00m eta 0:00:010:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 440.8/440.8 KB 13.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 133.7/133.7 KB 11.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 80.3/80.3 KB 7.8 MB/s eta 0:00:00
  

In [2]:
import tensorflow as tf
import os
import re
from collections import Counter
from sklearn.model_selection import train_test_split
from transformers import BertTokenizer, TFBertForSequenceClassification
import numpy as np


2024-04-04 11:39:08.960967: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2024-04-04 11:39:09.017145: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2024-04-04 11:39:09.018429: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-04-04 11:39:10.177090: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


Defining the necessary functions for loading the data and preprocessing the data

In [3]:
def load_data(file):
    data = []
    with open(file, 'r') as f:
        for line in f:
                line = line.strip()
                label = ' '.join(line[1:line.find("]")].strip().split())
                text = line[line.find("]")+1:].strip()
                data.append([label, text])
    return data
file = 'text.txt'
data = load_data(file)
print("Number of instances: {}".format(len(data)))
def tokenizer(token, n):
    output = []
    for i in range(len(token)-n+1):
        tokens = ' '.join(token[i:i+n])
        output.append(tokens)
    return output
def create_feature(text, nrange=(1, 1)):
    text_features = []
    text = text.lower()
    text_alphanum = re.sub('[^a-z)-9#]', ' ', text)
    for n in range(nrange[0], nrange[1]+1):
        text_features += tokenizer(text_alphanum.split(), n)
    text_punc = re.sub('[a-z0-9]', ' ', text)
    text_features += tokenizer(text_punc.split(), 1)
    return Counter(text_features)
def convert_label(item, name): 
    items = list(map(float, item.split()))
    label = ""
    for idx in range(len(items)): 
        if items[idx] == 1: 
            label += name[idx] + " "
    
    return label.strip()
emotions = ["joy", 'fear', "anger", "sadness", "disgust", "shame", "guilt"]

Number of instances: 7480


Loading the data and creating the feature vector

In [4]:
y_all = []
X_all = []
for label, text in data:
    y_all.append(convert_label(label, emotions))
    X_all.append(create_feature(text, nrange=(1, 4)))
count = {}
for i in emotions:
    count[i] = 0
for i in range(len(data)):
    count[y_all[i]] += 1
print(count)

{'joy': 1084, 'fear': 1078, 'anger': 1080, 'sadness': 1079, 'disgust': 1057, 'shame': 1045, 'guilt': 1057}


Splitting the data into training , validation and testing set

In [5]:
train_texts, test_texts, train_labels, test_labels = train_test_split(X_all, y_all, test_size=0.3, random_state=90)
test_texts, val_texts, test_labels, val_labels = train_test_split(test_texts, test_labels, test_size=0.3, random_state=90)
len_Tx = len(train_texts)
len_Ty = len(train_labels)
len_tx = len(test_texts)
len_ty = len(test_labels)
len_vx = len(val_texts)
len_vy = len(val_labels)
print({
    "X_train": len_Tx,
    "y_train": len_Ty,
    "X_test": len_tx,
    "y_test": len_ty,
    "X_val": len_vx,
    "y_val": len_vy
})


{'X_train': 5236, 'y_train': 5236, 'X_test': 1570, 'y_test': 1570, 'X_val': 674, 'y_val': 674}


In [6]:
model = TFBertForSequenceClassification.from_pretrained('bert-base-uncased')
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

batch_size = 32
learning_rate = 1e-5
num_epochs = 3


train_dataset = tf.data.Dataset.from_tensor_slices(({'input_ids': train_texts}, train_labels))
train_dataset = train_dataset.shuffle(buffer_size=len(train_texts)).batch(batch_size)

val_dataset = tf.data.Dataset.from_tensor_slices(({'input_ids': val_texts}, val_labels))
val_dataset = val_dataset.batch(batch_size)

test_dataset = tf.data.Dataset.from_tensor_slices(({'input_ids': test_texts}, test_labels))
test_dataset = test_dataset.batch(batch_size)

optimizer = tf.keras.optimizers.Adam(learning_rate=learning_rate)
loss = tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True)

model.compile(optimizer=optimizer, loss=loss, metrics=['accuracy'])

model.fit(train_dataset, epochs=num_epochs, validation_data=val_dataset)

results = model.evaluate(test_dataset)
print("Test accuracy:", results[1])


config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/440M [00:00<?, ?B/s]

2024-04-04 11:39:28.562989: I tensorflow/compiler/xla/stream_executor/cuda/cuda_gpu_executor.cc:995] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355
2024-04-04 11:39:28.565115: W tensorflow/core/common_runtime/gpu/gpu_device.cc:1960] Cannot dlopen some GPU libraries. Please make sure the missing libraries mentioned above are installed properly if you would like to use GPU. Follow the guide at https://www.tensorflow.org/install/gpu for how to download and setup the required libraries for your platform.
Skipping registering GPU devices...
All PyTorch model weights were used when initializing TFBertForSequenceClassification.

Some weights or buffers of the TF 2.0 model TFBertForSequenceClassification were not initialized from the PyTorch model and are newly initialized: ['classifier.weight', 'classifi

tokenizer_config.json:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

ValueError: Attempt to convert a value (Counter({'when': 1, 'my': 1, 'friend': 1, 'did': 1, 'not': 1, 'pass': 1, 'the': 1, 'high': 1, 'school': 1, 'graduation': 1, 'examinations.': 1, 'when my': 1, 'my friend': 1, 'friend did': 1, 'did not': 1, 'not pass': 1, 'pass the': 1, 'the high': 1, 'high school': 1, 'school graduation': 1, 'graduation examinations.': 1, 'when my friend': 1, 'my friend did': 1, 'friend did not': 1, 'did not pass': 1, 'not pass the': 1, 'pass the high': 1, 'the high school': 1, 'high school graduation': 1, 'school graduation examinations.': 1, 'when my friend did': 1, 'my friend did not': 1, 'friend did not pass': 1, 'did not pass the': 1, 'not pass the high': 1, 'pass the high school': 1, 'the high school graduation': 1, 'high school graduation examinations.': 1, '.': 1})) with an unsupported type (<class 'collections.Counter'>) to a Tensor.